In [2]:
# Langkah awal: Import library
import pandas as pd

# Upload file dari Google Drive (pastikan kamu sudah mount Drive)
from google.colab import drive
drive.mount('/content/drive')

# Ganti path ini dengan path ke file CSV-mu
path = '/content/IMDB Dataset.csv'

# Baca data
df = pd.read_csv(path)
df.head()


Mounted at /content/drive


review sentiment
0  One of the other reviewers has mentioned that ...  positive
1  A wonderful little production. <br /><br />The...  positive
2  I thought this was a wonderful way to spend ti...  positive
3  Basically there's a family where a little boy ...  negative
4  Petter Mattei's "Love in the Time of Money" is...  positive

In [3]:
!pip install textblob
from textblob import TextBlob

# Tambahkan kolom baru untuk prediksi sentimen
df['predicted_sentiment'] = df['review'].apply(lambda x: TextBlob(x).sentiment.polarity)

# Konversi nilai ke positif/negatif
df['predicted_sentiment'] = df['predicted_sentiment'].apply(lambda x: 'positive' if x > 0 else 'negative')

# Lihat hasil
df[['review', 'sentiment', 'predicted_sentiment']].head()


review sentiment  \
0  One of the other reviewers has mentioned that ...  positive   
1  A wonderful little production. <br /><br />The...  positive   
2  I thought this was a wonderful way to spend ti...  positive   
3  Basically there's a family where a little boy ...  negative   
4  Petter Mattei's "Love in the Time of Money" is...  positive   

  predicted_sentiment  
0            positive  
1            positive  
2            positive  
3            negative  
4            positive

In [4]:
!pip install transformers
!pip install sentencepiece


In [5]:
from transformers import PegasusTokenizer, PegasusForConditionalGeneration
import torch

# Load tokenizer dan model
model_name = "google/pegasus-xsum"
tokenizer = PegasusTokenizer.from_pretrained(model_name)
model = PegasusForConditionalGeneration.from_pretrained(model_name)


/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/87.0 [00:00<?, ?B/s]

spiece.model:   0%|          | 0.00/1.91M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/65.0 [00:00<?, ?B/s]

tokenizer.json: 0.00B [00:00, ?B/s]

config.json: 0.00B [00:00, ?B/s]

pytorch_model.bin:   0%|          | 0.00/2.28G [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/2.28G [00:00<?, ?B/s]

Some weights of PegasusForConditionalGeneration were not initialized from the model checkpoint at google/pegasus-xsum and are newly initialized: ['model.decoder.embed_positions.weight', 'model.encoder.embed_positions.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


generation_config.json:   0%|          | 0.00/259 [00:00<?, ?B/s]

In [6]:
def summarize_text(text):
    # Tokenisasi
    tokens = tokenizer(text, truncation=True, padding='longest', return_tensors="pt")

    # Generate ringkasan
    summary_ids = model.generate(**tokens, max_length=50, num_beams=4, length_penalty=2.0)
    summary = tokenizer.decode(summary_ids[0], skip_special_tokens=True)
    return summary


In [7]:
# Coba ringkas 5 review pertama
sample_reviews = df['review'].head(5)

summaries = [summarize_text(review) for review in sample_reviews]

# Gabung ke dataframe
df_summary = pd.DataFrame({
    'Original Review': sample_reviews,
    'Summary': summaries
})

df_summary


Original Review  \
0  One of the other reviewers has mentioned that ...   
1  A wonderful little production. <br /><br />The...   
2  I thought this was a wonderful way to spend ti...   
3  Basically there's a family where a little boy ...   
4  Petter Mattei's "Love in the Time of Money" is...   

                                             Summary  
0  Oz the Great and Powerful is one of the most t...  
1  br />br />This is a wonderful production about...  
2  Woody Allen's latest film, "You Will Meet a Ta...  
3  I've been to the cinema for the first time in ...  
4  It is not every day that you get the chance to...

from matplotlib import pyplot as plt
import seaborn as sns
df_summary.groupby('Original Review').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
df_summary.groupby('Summary').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
import pandas as pd
plt.subplots(figsize=(8, 8))
df_2dhist = pd.DataFrame({
    x_label: grp['Summary'].value_counts()
    for x_label, grp in df_summary.groupby('Original Review')
})
sns.heatmap(df_2dhist, cmap='viridis')
plt.xlabel('Original Review')
_ = plt.ylabel('Summary')

from matplotlib import pyplot as plt
_df_0['index'].plot(kind='hist', bins=20, title='index')
plt.gca().spines[['top', 'right',]].set_visible(False)

...

from matplotlib import pyplot as plt
import seaborn as sns
import pandas as pd
plt.subplots(figsize=(8, 8))
df_2dhist = pd.DataFrame({
    x_label: grp['Summary'].value_counts()
    for x_label, grp in _df_6.groupby('Original Review')
})
sns.heatmap(df_2dhist, cmap='viridis')
plt.xlabel('Original Review')
_ = plt.ylabel('Summary')

<string>:5: FutureWarning: 

Passing `palette` without assigning `hue` is deprecated and will be removed in v0.14.0. Assign the `y` variable to `hue` and set `legend=False` for the same effect.



from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_7['Original Review'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_7, x='index', y='Original Review', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

<string>:5: FutureWarning: 

Passing `palette` without assigning `hue` is deprecated and will be removed in v0.14.0. Assign the `y` variable to `hue` and set `legend=False` for the same effect.



from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_8['Summary'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_8, x='index', y='Summary', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)